In [1]:
import torch
from bin.model import BrainMimic
import networkx as nx
import nibabel as nib
import pandas as pd
import json
import os

220601-18:38:34,778 nipype.utils WARNING:
	 A newer version (1.8.1) of nipy/nipype is available. You are using 1.6.1


Intel(R) Extension for Scikit-learn* enabled (https://github.com/intel/scikit-learn-intelex)


In [2]:
structure_graph_path = '../MTurk1/misc_testing_files/rep_geo_corr_graph_thresholded.json' # path to shape color graph
data = json.load(open(structure_graph_path, 'r'))
gt = nx.readwrite.node_link_graph(data)
# gt = gt.subgraph(list(gt.nodes())[:15])
# gt = gt.subgraph(sorted(nx.connected_components(gt), key=len, reverse=True)[0])
# nx.draw(gt)

In [3]:
# refine graph
desired_rois = ['visual-area-1', 'visual-area-2', 'visual-area-3', 'visual-area-4',
                'middle-temporal', 'inferior-temporal', 'area-TEO', 'superior-temporal',
                'sts-dorsal', 'caudate', 'putamen', 'claustrum', 'globus-pallidus',
                'insula', 'reticular-nucleus', 'posterior-TE', 'anterior-TE', 'perirhinal-cortex',
                'entorhinal-cortex', 'substantia-nigra', 'red-nucleus', 'ventro-lateral-prefrontal',
                'dorso-lateral-prefrontal', 'medial-prefrontal', 'orbital-prefrontal',
                'cingulate-cortex', 'periarcuate-area', 'temporal-pole', 'temporal-gyrus',
                'sts-fundus', 'sts-ventral']
net_nodes = set()
for n in gt.nodes():
    if True in [roi in gt.nodes[n]['roi_name'] for roi in desired_rois]:
        net_nodes.add(n)

gt = gt.subgraph(net_nodes)
gt = gt.subgraph(sorted(nx.connected_components(gt), key=len, reverse=True)[0])
gt = gt.copy()
gt.remove_nodes_from([224, 285, 293, 301, 233])

In [4]:
roi_atlas = nib.load('/Users/loggiasr/Projects/fmri/monkey_fmri/MTurk1/D99_v2.0_dist/reg_D99_atlas_v2.0.nii.gz')

In [5]:
start_node = None
for n, data in gt.nodes(data=True):
    if data['roi_name'] == 'visual-area-1-(primary-visual-cortex)':
        start_node = n
        break
echo = BrainMimic(gt, start_node, units_per_voxel=10, stimuli_shape=(1, 3, 64, 64))

added computational node 0 putamen with size (1, 53, 16, 16)
added computational node 1 caudate-nucleus with size (1, 45, 16, 16)
added computational node 3 globus-pallidus-external-segment with size (1, 220, 4, 4)
added computational node 4 globus-pallidus-internal-segment with size (1, 98, 4, 4)
added computational node 5 substantia-nigra-pars-reticulata with size (1, 15, 8, 8)
added computational node 6 substantia-nigra-pars-compacta with size (1, 6, 8, 8)
added computational node 7 substantia-nigra-pars-lateralis with size (1, 40, 2, 2)
added computational node 33 reticular-nucleus with size (1, 6, 16, 16)
added computational node 36 red-nucleus,-parvicellular-division with size (1, 7, 8, 8)
added computational node 74 red-nucleus,-magnocellular-division with size (1, 2, 8, 8)
added computational node 131 dorsomedial-prefrontal-area-- with size (1, 2, 32, 32)
added computational node 132 orbital-prefrontal-area with size (1, 7, 16, 16)
added computational node 134 orbito-medial-pre

In [6]:
# load paradigm data
from PIL import Image
import numpy as np
path = '../MTurk1/stimuli/small_stimuli'
chromatic_colored_path = os.path.join(path, 'chromatic_colored')
chromatic_uncolored_path = os.path.join(path, 'chromatic_uncolored')
achromatic_path = os.path.join(path, 'achromatic')
colored_circle_path = os.path.join(path, 'colored_circle')

condition_paths = [chromatic_uncolored_path, chromatic_colored_path, achromatic_path, colored_circle_path]

stimuli = []

for path in condition_paths:
    stimuli.append([torch.from_numpy(np.array(Image.open(os.path.join(path, f))).transpose((2, 0, 1))[None, :, :, :]) for f in sorted(os.listdir(path)) if '.png' in f])


In [ ]:

echo.fit_rdms(stimuli, epochs=50, stimulus_frames=10, verbose=True)

presenting cond  tensor(2) frame 0
computing inputs to node orbital-prefrontal-area  on epoch 0
computing inputs to node subregion-of-anterior-cingulate-cortex--  on epoch 0
computing inputs to node posterolateral-agranular-insula-area--  on epoch 0
computing inputs to node visual-area-2-(or-transition-area-?)  on epoch 0
computing inputs to node sts-dorsal-bank-area  on epoch 0
computing inputs to node medial-prefrontal-area  on epoch 0
computing inputs to node granular-part-of-the-dorsal-temporal-pole-  on epoch 0
computing inputs to node subregion-of-posterior-cingulate-cortex  on epoch 0
computing inputs to node caudate-nucleus  on epoch 0
computing inputs to node sts-ventral-bank-area-  on epoch 0
computing inputs to node medial-agranular-insula-area  on epoch 0
computing inputs to node parainsular-area  on epoch 0
computing inputs to node orbital-prefrontal-area  on epoch 0
computing inputs to node subregion-of-anterior-cingulate-cortex  on epoch 0
computing inputs to node medial

In [5]:
brain_echo = nx.read_gpickle("/Users/loggiasr/Projects/fmri/monkey_fmri/MTurk1/misc_testing_files/brain_mimic_epoch_24")